<span style="color: blue">Author:A Nikfarjma</span>

## <span style="color: yellow">Data Source and description</span>

**Source:** 
Data has been Collected from NCBI's(The National Center for Biotechnology Information) GEO(Gene Expression Omnibus) DataSet.

https://www.ncbi.nlm.nih.gov/geo/query/acc.cgi?acc=GSE62944

NCBI GEO Accession Number: GSE62944

This data is consist of RNA-Seq data for 9264 tumor samples and 741 normal samples across 24 cancer types from The Cancer Genome Atlas with "Rsubread"

Lets Take a look!

There are two text file in the data set that contain the sample name for cancerous and normal samples with their respective ids.



Also data has been normalize using RNA sequincing methis FPKM and TPM. For building a classification model, the choice between raw counts, FPKM, or TPM depends on the specific requirements of our analysis and the algorithms we plan to use. Raw counts are often preferred for differential expression analysis using tools like DESeq2 or edgeR, as these methods have their own normalization procedures. However, since our classification model or downstream analysis requires normalized expression values, TPM is generally favored over FPKM because TPM accounts for sequencing depth and gene length, facilitating more accurate comparisons across samples. It's crucial to ensure that the data format and normalization method align with the assumptions of your chosen analytical tools.

In [1]:
#normal smaples
with open("./data/NormalSample.txt", "r") as file:
    data = [line.strip().split("\t") for line in file]

# Print first 3 rows
print(data[:3])

[['TCGA-K4-A3WV-11A-21R-A22U-07', 'BLCA'], ['TCGA-49-6742-11A-01R-1858-07', 'LUAD'], ['TCGA-DD-A3A2-11A-11R-A213-07', 'LIHC']]


<span style="color: green">Now lets map these genes</span>

In [2]:
#lets extract unique values of the genes
unique_genes=set()
for sample in data:
    if sample[1] not in unique_genes:
        unique_genes.add(sample[1])
unique_genes


{'BLCA',
 'BRCA',
 'CESC',
 'CHOL',
 'COAD',
 'ESCA',
 'GBM',
 'HNSC',
 'KICH',
 'KIRC',
 'KIRP',
 'LIHC',
 'LUAD',
 'LUSC',
 'PAAD',
 'PCPG',
 'PRAD',
 'READ',
 'SARC',
 'SKCM',
 'STAD',
 'THCA',
 'THYM',
 'UCEC'}

it seams like the only gene related to breast cancer here is **BRCA**

In [3]:
#extracting all the BRCA samples

#healthy_brca_samples=set()
healthy_genes_sample_dic={gene:[] for gene in unique_genes}
# Populate dictionary
for sample_id, cancer_type in data:
    if cancer_type in healthy_genes_sample_dic:
        healthy_genes_sample_dic[cancer_type].append(sample_id)



In [4]:
healthy_genes_sample_dic

{'PRAD': ['TCGA-EJ-7781-11A-01R-2118-07',
  'TCGA-CH-5769-11A-01R-1580-07',
  'TCGA-EJ-7317-11A-01R-2118-07',
  'TCGA-G9-6496-11A-01R-1789-07',
  'TCGA-G9-6365-11A-01R-1789-07',
  'TCGA-EJ-7314-11A-01R-2118-07',
  'TCGA-HC-7747-11A-01R-2118-07',
  'TCGA-EJ-7123-11A-01R-1965-07',
  'TCGA-EJ-7315-11A-01R-2118-07',
  'TCGA-CH-5761-11A-01R-1580-07',
  'TCGA-EJ-7789-11A-01R-2118-07',
  'TCGA-EJ-7115-11A-01R-2118-07',
  'TCGA-G9-6356-11A-01R-1789-07',
  'TCGA-EJ-A8FO-11A-11R-A36G-07',
  'TCGA-EJ-7783-11A-01R-2118-07',
  'TCGA-CH-5768-11A-01R-1580-07',
  'TCGA-EJ-7327-11A-01R-2118-07',
  'TCGA-EJ-7792-11A-01R-2118-07',
  'TCGA-EJ-7794-11A-01R-2118-07',
  'TCGA-HC-7740-11A-01R-2118-07',
  'TCGA-EJ-7793-11A-01R-2263-07',
  'TCGA-EJ-7785-11A-01R-2118-07',
  'TCGA-G9-6333-11A-01R-1965-07',
  'TCGA-HC-8259-11A-01R-2263-07',
  'TCGA-G9-6351-11A-01R-1965-07',
  'TCGA-HC-7745-11A-01R-2118-07',
  'TCGA-EJ-7125-11A-01R-1965-07',
  'TCGA-EJ-7331-11A-01R-2118-07',
  'TCGA-G9-6384-11A-01R-1858-07',
  'TCG

now we maped all the samples for healthy genes now lets look at the cancerous ones

In [5]:
with open("./data/CancerousSaples.txt", "r") as file:
    data = [line.strip().split("\t") for line in file]
cUnique_genes=set()
for sample in data:
    if sample[1] not in cUnique_genes:
        cUnique_genes.add(sample[1])

cancerous_genes_sample_dic={gene:[] for gene in unique_genes}
# Populate dictionary
for sample_id, cancer_type in data:
    if cancer_type in cancerous_genes_sample_dic:
        cancerous_genes_sample_dic[cancer_type].append(sample_id)
cancerous_genes_sample_dic

{'PRAD': ['TCGA-G9-A9S0-01A-11R-A41O-07',
  'TCGA-XK-AAIW-01A-11R-A41O-07',
  'TCGA-J4-A67M-01A-11R-A30B-07',
  'TCGA-J4-A67Q-01A-21R-A30B-07',
  'TCGA-XJ-A83G-01A-11R-A352-07',
  'TCGA-H9-A6BY-01A-11R-A30B-07',
  'TCGA-KK-A59Z-01A-12R-A26U-07',
  'TCGA-EJ-A65M-01A-11R-A29R-07',
  'TCGA-CH-5748-01A-11R-1580-07',
  'TCGA-HC-A9TE-01A-11R-A41O-07',
  'TCGA-J9-A52C-01A-11R-A26U-07',
  'TCGA-G9-6371-01A-11R-1789-07',
  'TCGA-EJ-A46E-01A-31R-A250-07',
  'TCGA-CH-5764-01A-21R-1580-07',
  'TCGA-M7-A721-01A-12R-A32O-07',
  'TCGA-KK-A6DY-01A-12R-A311-07',
  'TCGA-ZG-A9LU-01A-11R-A41O-07',
  'TCGA-FC-7961-01A-11R-A29R-07',
  'TCGA-XJ-A9DK-01A-11R-A37L-07',
  'TCGA-VN-A88Q-01A-11R-A352-07',
  'TCGA-KK-A7AP-01A-12R-A33R-07',
  'TCGA-HC-A48F-01A-11R-A250-07',
  'TCGA-HC-8265-01B-04R-2302-07',
  'TCGA-ZG-A9LZ-01A-11R-A41O-07',
  'TCGA-V1-A9ZG-01A-11R-A41O-07',
  'TCGA-G9-6362-01A-11R-1789-07',
  'TCGA-G9-A9S7-01A-11R-A41O-07',
  'TCGA-J4-A83N-01A-11R-A352-07',
  'TCGA-KC-A4BR-01A-32R-A32Y-07',
  'TCG

Now we have referances to samples and genes lets extract all the BRCA samples

In [6]:
# lets look at GSM1536837_01_27_15_TCGA_20.Illumina.tumor_Rsubread_TPM
with open('data/GSE62944_RAW/GSM1536837_06_01_15_TCGA_24.tumor_Rsubread_TPM.txt','r') as file:
    feature_data=[line.strip().split("\t") for line in file]

feature_data[0][-3:-1]

['TCGA-ZS-A9CF-02A-11R-A38B-07', 'TCGA-ZS-A9CG-01A-11R-A37K-07']

## <span style="color: yellow">

In [7]:
len(data)

9264

In [8]:
import pandas as pd

df = pd.DataFrame(feature_data)

df.head()

0                             1     \
0  TCGA-02-0047-01A-01R-1849-01  TCGA-02-0055-01A-01R-1849-01   
1                   1/2-SBSRNA4              2.34180779897709   
2                          A1BG              11.7173931223676   
3                      A1BG-AS1              1.33274150888264   
4                          A1CF           0.00783961263378836   

                           2                             3     \
0  TCGA-02-2483-01A-01R-1849-01  TCGA-02-2485-01A-01R-1849-01   
1              1.64575215578575              2.43263380829254   
2              24.7763572132346              20.2648719245462   
3              1.08603706301478              1.09297209133143   
4             0.015495311808889           0.00479039331850954   

                           4                             5     \
0  TCGA-02-2486-01A-01R-1849-01  TCGA-04-1331-01A-01R-1569-13   
1              2.04036406475485              1.40859926165477   
2               5.1177123833555              5.95979586986965   
3             0.707189363771972             0.608536246570792   
4           0.00585469442145148           0.00544099991686763   

                           6                             7     \
0  TCGA-04-1332-01A-01R-1564-13  TCGA-04-1337-01A-01R-1564-13   
1              4.08500123669713              1.64344250568849   
2              22.4929513168985              4.26866974722146   
3              3.29101508083205             0.636544632484977   
4            0.0235780321144235            0.0284571322739637   

                           8                             9     ...  \
0  TCGA-04-1338-01A-01R-1564-13  TCGA-04-1341-01A-01R-1564-13  ...   
1              4.17885803869778              1.73244853368479  ...   
2              9.32833631054866              7.55995847739945  ...   
3              1.93088255678914             0.696446879034295  ...   
4            0.0190765373788806            0.0366295297288906  ...   

                           9255                          9256  \
0  TCGA-ZP-A9D2-01A-11R-A38B-07  TCGA-ZP-A9D4-01A-11R-A37K-07   
1             0.347388825555485             0.733966333074115   
2              2322.58593459571              43.9997958639196   
3              7.02361491668872             0.453430961753005   
4               48.594490263584              37.4965936190835   

                           9257                          9258  \
0  TCGA-ZQ-A9CR-01A-11R-A39E-31  TCGA-ZS-A9CD-01A-11R-A37K-07   
1             0.853099951263001             0.814110159868275   
2              1793.07061325774              4.85285257810494   
3              9.41200210705638             0.388637270859652   
4              59.8263832981506              2.09513329984465   

                           9259                          9260  \
0  TCGA-ZS-A9CE-01A-11R-A37K-07  TCGA-ZS-A9CF-01A-11R-A38B-07   
1             0.236654111917491             0.456498091772548   
2              2033.96723633235              3907.83790754622   
3              8.52748094151365              9.08861178822967   
4              27.4178826337677              40.4449662284777   

                           9261                          9262  \
0  TCGA-ZS-A9CF-02A-11R-A38B-07  TCGA-ZS-A9CG-01A-11R-A37K-07   
1               2.0007951391706              4.18063767545344   
2              544.860528291095              233.078057214062   
3              4.04526960884422              1.95248795513533   
4              68.4793019038917              96.5849604190457   

                           9263                 9264  
0  TCGA-ZX-AA5X-01A-11R-A42T-07                 None  
1             0.509342962675824     1.48192576535246  
2              580.658764687128     5.78202791256206  
3              2.99579748187921     1.50919876535332  
4              60.2122597568698  0.00992201320489947  

[5 rows x 9265 columns]

need to drop the first row and set the second one as header and shift them one column over

In [ ]:
# Creating the DataFrame
moded_df = pd.DataFrame(feature_data)

# Extract first row as column names and shift right
new_columns = [""] + moded_df.iloc[0, :-1].tolist()  # Shift column names one position right

# Drop the first row since it's now the header
moded_df = moded_df.iloc[1:].reset_index(drop=True)

# Assign the new column names
moded_df.columns = new_columns

moded_df.head()

TCGA-02-0047-01A-01R-1849-01 TCGA-02-0055-01A-01R-1849-01  \
0  1/2-SBSRNA4             2.34180779897709             1.64575215578575   
1         A1BG             11.7173931223676             24.7763572132346   
2     A1BG-AS1             1.33274150888264             1.08603706301478   
3         A1CF          0.00783961263378836            0.015495311808889   
4        A2LD1             3.03652529001364             3.10263327586671   

  TCGA-02-2483-01A-01R-1849-01 TCGA-02-2485-01A-01R-1849-01  \
0             2.43263380829254             2.04036406475485   
1             20.2648719245462              5.1177123833555   
2             1.09297209133143            0.707189363771972   
3          0.00479039331850954          0.00585469442145148   
4             1.43091177120877             6.13049025914624   

  TCGA-02-2486-01A-01R-1849-01 TCGA-04-1331-01A-01R-1569-13  \
0             1.40859926165477             4.08500123669713   
1             5.95979586986965             22.4929513168985   
2            0.608536246570792             3.29101508083205   
3          0.00544099991686763           0.0235780321144235   
4             6.05450592575091             3.52917089274419   

  TCGA-04-1332-01A-01R-1564-13 TCGA-04-1337-01A-01R-1564-13  \
0             1.64344250568849             4.17885803869778   
1             4.26866974722146             9.32833631054866   
2            0.636544632484977             1.93088255678914   
3           0.0284571322739637           0.0190765373788806   
4             2.97042467356097             3.58488583814053   

  TCGA-04-1338-01A-01R-1564-13  ... TCGA-ZP-A9D1-01A-11R-A38B-07  \
0             1.73244853368479  ...            0.347388825555485   
1             7.55995847739945  ...             2322.58593459571   
2            0.696446879034295  ...             7.02361491668872   
3           0.0366295297288906  ...              48.594490263584   
4             3.78740883457729  ...             5.46423253889593   

  TCGA-ZP-A9D2-01A-11R-A38B-07 TCGA-ZP-A9D4-01A-11R-A37K-07  \
0            0.733966333074115            0.853099951263001   
1             43.9997958639196             1793.07061325774   
2            0.453430961753005             9.41200210705638   
3             37.4965936190835             59.8263832981506   
4             10.4344641043496             3.85912874382051   

  TCGA-ZQ-A9CR-01A-11R-A39E-31 TCGA-ZS-A9CD-01A-11R-A37K-07  \
0            0.814110159868275            0.236654111917491   
1             4.85285257810494             2033.96723633235   
2            0.388637270859652             8.52748094151365   
3             2.09513329984465             27.4178826337677   
4             2.34831379648535             5.89794546122663   

  TCGA-ZS-A9CE-01A-11R-A37K-07 TCGA-ZS-A9CF-01A-11R-A38B-07  \
0            0.456498091772548              2.0007951391706   
1             3907.83790754622             544.860528291095   
2             9.08861178822967             4.04526960884422   
3             40.4449662284777             68.4793019038917   
4             9.18921577523948             10.4562840780572   

  TCGA-ZS-A9CF-02A-11R-A38B-07 TCGA-ZS-A9CG-01A-11R-A37K-07  \
0             4.18063767545344            0.509342962675824   
1             233.078057214062             580.658764687128   
2             1.95248795513533             2.99579748187921   
3             96.5849604190457             60.2122597568698   
4             12.9114147880195             7.08272708139775   

  TCGA-ZX-AA5X-01A-11R-A42T-07  
0             1.48192576535246  
1             5.78202791256206  
2             1.50919876535332  
3          0.00992201320489947  
4              3.0288867847545  

[5 rows x 9265 columns]

In [10]:
moded_df=moded_df.set_index(moded_df.columns[0])
moded_df.head()

TCGA-02-0047-01A-01R-1849-01 TCGA-02-0055-01A-01R-1849-01  \
                                                                        
1/2-SBSRNA4             2.34180779897709             1.64575215578575   
A1BG                    11.7173931223676             24.7763572132346   
A1BG-AS1                1.33274150888264             1.08603706301478   
A1CF                 0.00783961263378836            0.015495311808889   
A2LD1                   3.03652529001364             3.10263327586671   

            TCGA-02-2483-01A-01R-1849-01 TCGA-02-2485-01A-01R-1849-01  \
                                                                        
1/2-SBSRNA4             2.43263380829254             2.04036406475485   
A1BG                    20.2648719245462              5.1177123833555   
A1BG-AS1                1.09297209133143            0.707189363771972   
A1CF                 0.00479039331850954          0.00585469442145148   
A2LD1                   1.43091177120877             6.13049025914624   

            TCGA-02-2486-01A-01R-1849-01 TCGA-04-1331-01A-01R-1569-13  \
                                                                        
1/2-SBSRNA4             1.40859926165477             4.08500123669713   
A1BG                    5.95979586986965             22.4929513168985   
A1BG-AS1               0.608536246570792             3.29101508083205   
A1CF                 0.00544099991686763           0.0235780321144235   
A2LD1                   6.05450592575091             3.52917089274419   

            TCGA-04-1332-01A-01R-1564-13 TCGA-04-1337-01A-01R-1564-13  \
                                                                        
1/2-SBSRNA4             1.64344250568849             4.17885803869778   
A1BG                    4.26866974722146             9.32833631054866   
A1BG-AS1               0.636544632484977             1.93088255678914   
A1CF                  0.0284571322739637           0.0190765373788806   
A2LD1                   2.97042467356097             3.58488583814053   

            TCGA-04-1338-01A-01R-1564-13 TCGA-04-1341-01A-01R-1564-13  ...  \
                                                                       ...   
1/2-SBSRNA4             1.73244853368479            0.948406127013232  ...   
A1BG                    7.55995847739945             14.1505845997296  ...   
A1BG-AS1               0.696446879034295            0.435584084750929  ...   
A1CF                  0.0366295297288906           0.0126998238857055  ...   
A2LD1                   3.78740883457729             1.73694772371811  ...   

            TCGA-ZP-A9D1-01A-11R-A38B-07 TCGA-ZP-A9D2-01A-11R-A38B-07  \
                                                                        
1/2-SBSRNA4            0.347388825555485            0.733966333074115   
A1BG                    2322.58593459571             43.9997958639196   
A1BG-AS1                7.02361491668872            0.453430961753005   
A1CF                     48.594490263584             37.4965936190835   
A2LD1                   5.46423253889593             10.4344641043496   

            TCGA-ZP-A9D4-01A-11R-A37K-07 TCGA-ZQ-A9CR-01A-11R-A39E-31  \
                                                                        
1/2-SBSRNA4            0.853099951263001            0.814110159868275   
A1BG                    1793.07061325774             4.85285257810494   
A1BG-AS1                9.41200210705638            0.388637270859652   
A1CF                    59.8263832981506             2.09513329984465   
A2LD1                   3.85912874382051             2.34831379648535   

            TCGA-ZS-A9CD-01A-11R-A37K-07 TCGA-ZS-A9CE-01A-11R-A37K-07  \
                                                                        
1/2-SBSRNA4            0.236654111917491            0.456498091772548   
A1BG                    2033.96723633235             3907.83790754622   
A1BG-AS1                8.52748094151365             9.08861178822967   
A1CF                    27.4

Now we have all the samples and genes that showed up in cancerous data

In [11]:
moded_df.index

Index(['1/2-SBSRNA4', 'A1BG', 'A1BG-AS1', 'A1CF', 'A2LD1', 'A2M', 'A2ML1',
       'A2MP1', 'A4GALT', 'A4GNT',
       ...
       'ZWINT', 'ZXDA', 'ZXDB', 'ZXDC', 'ZYG11A', 'ZYG11B', 'ZYX', 'ZZEF1',
       'ZZZ3', 'tAKR'],
      dtype='object', name='', length=23368)

<span style="color: green">the indecies are feature id</span>

Now that we have all the samples seperated in healthy and non healthy genes sample we can alsi extract dates using enterez api. and get dates of sample esxtraction and use for analysis like the evolution of cancer. Meaning How genes matation changes as time passes. 

In [2]:
from Bio import Entrez
import ssl
import Bio
import pandas as pd
# Disable SSL verification (for development purposes)
ssl._create_default_https_context = ssl._create_unverified_context
Entrez.email = "ashkan.nikfarjam@sjsu.edu"



In [15]:
import xml.etree.ElementTree as ET
# List to store row-wise structured data
times_series_sample_healthy = []

# Loop through each gene and its associated samples
for gene, samples in healthy_genes_sample_dic.items():
    for sample in samples:
        # Search for the sample in BioSample database
        handle = Entrez.esearch(db="biosample", term=sample)
        record = Entrez.read(handle)
        handle.close()

        collection_date = "Not found"  # Default value

        if record["IdList"]:
            biosample_id = record["IdList"][0]

            # Fetch metadata
            handle = Entrez.efetch(db="biosample", id=biosample_id, rettype="xml")
            biosample_data = handle.read()
            handle.close()

            # Parse XML to extract collection date
            root = ET.fromstring(biosample_data)

            for attribute in root.iter("Attribute"):
                if "harmonized_name" in attribute.attrib and attribute.attrib["harmonized_name"] == "collection date":
                    collection_date = attribute.text
                    break
        
        # Append structured data to list
        times_series_sample_healthy.append({
            "Gene": gene,
            "Sample": sample,
            "Collection_Date": collection_date
        })

# Convert list of dictionaries to DataFrame
df_date_healthy = pd.DataFrame(times_series_sample_healthy)

df_date_healthy.head()

Gene                        Sample Collection_Date
0  PRAD  TCGA-EJ-7781-11A-01R-2118-07       Not found
1  PRAD  TCGA-CH-5769-11A-01R-1580-07       Not found
2  PRAD  TCGA-EJ-7317-11A-01R-2118-07       Not found
3  PRAD  TCGA-G9-6496-11A-01R-1789-07       Not found
4  PRAD  TCGA-G9-6365-11A-01R-1789-07       Not found

In [16]:
df_date_healthy[df_date_healthy['Gene']=='BRCA'].shape

(113, 3)

In [17]:
cancerous_genes_sample_dic['BRCA']

['TCGA-A2-A0T1-01A-21R-A084-07',
 'TCGA-A7-A3J0-01A-11R-A213-07',
 'TCGA-AO-A126-01A-11R-A10J-07',
 'TCGA-E2-A14X-01A-11R-A115-07',
 'TCGA-A7-A13G-01A-11R-A13Q-07',
 'TCGA-AR-A0TP-01A-11R-A084-07',
 'TCGA-E2-A15S-01A-11R-A115-07',
 'TCGA-A2-A1FW-01A-11R-A13Q-07',
 'TCGA-HN-A2OB-01A-21R-A27Q-07',
 'TCGA-B6-A0I1-01A-11R-A21T-07',
 'TCGA-LL-A440-01A-11R-A24H-07',
 'TCGA-E2-A14T-01A-11R-A115-07',
 'TCGA-LL-A740-01A-21R-A32P-07',
 'TCGA-BH-A5IZ-01A-11R-A27Q-07',
 'TCGA-E9-A1N5-01A-11R-A14D-07',
 'TCGA-BH-A18L-01A-32R-A12D-07',
 'TCGA-GM-A2DC-01A-11R-A18M-07',
 'TCGA-E9-A1NC-01A-21R-A26B-07',
 'TCGA-BH-A0C0-01A-21R-A056-07',
 'TCGA-A2-A0EU-01A-22R-A056-07',
 'TCGA-AR-A24U-01A-11R-A169-07',
 'TCGA-A8-A096-01A-11R-A00Z-07',
 'TCGA-EW-A1PG-01A-11R-A144-07',
 'TCGA-D8-A1XJ-01A-11R-A14M-07',
 'TCGA-A8-A082-01A-11R-A00Z-07',
 'TCGA-A2-A3KD-01A-12R-A213-07',
 'TCGA-GM-A2DK-01A-21R-A180-07',
 'TCGA-B6-A0WY-01A-11R-A109-07',
 'TCGA-E2-A159-01A-11R-A115-07',
 'TCGA-A8-A06P-01A-11R-A00Z-07',
 'TCGA-BH-

In [18]:
BRCA_mutated_data=moded_df.loc[:,cancerous_genes_sample_dic['BRCA']]
BRCA_mutated_data

TCGA-A2-A0T1-01A-21R-A084-07 TCGA-A7-A3J0-01A-11R-A213-07  \
                                                                        
1/2-SBSRNA4            0.960894001732585             1.79708641615056   
A1BG                    3.55441830878723             24.8511023337201   
A1BG-AS1                1.12624073442509             3.72311870425808   
A1CF                 0.00839155127969162                            0   
A2LD1                   4.55869505679023             6.19852777232165   
...                                  ...                          ...   
ZYG11B                    10.87191636006             12.2433532160665   
ZYX                     365.273345093633             152.190474694495   
ZZEF1                   12.1084963137152             27.4519209528469   
ZZZ3                    12.3560827093021             22.9930017584635   
tAKR                   0.114478299419014             0.11398842097193   

            TCGA-AO-A126-01A-11R-A10J-07 TCGA-E2-A14X-01A-11R-A115-07  \
                                                                        
1/2-SBSRNA4             2.48136842272879             1.25877918887833   
A1BG                    37.6048986305345             3.14831871353749   
A1BG-AS1                1.53058196884434             1.78370238476053   
A1CF                  0.0295666343487768           0.0486228954429215   
A2LD1                   5.50420560541654             6.27771883565517   
...                                  ...                          ...   
ZYG11B                  9.13528384909196             18.6954742347446   
ZYX                     254.570884887423             227.541749180432   
ZZEF1                   5.88806299340222             16.2859268370279   
ZZZ3                    23.8344923927268             44.8001213375898   
tAKR                  0.0864322912494616            0.154774182521078   

            TCGA-A7-A13G-01A-11R-A13Q-07 TCGA-AR-A0TP-01A-11R-A084-07  \
                                                                        
1/2-SBSRNA4                2.31111187622             2.23687134793837   
A1BG                    4.08870963418863             11.8845011062784   
A1BG-AS1                1.72553127179168             2.11927465153879   
A1CF                   0.341331734325332           0.0146510597853031   
A2LD1                   2.52092239644118             4.61679472085385   
...                                  ...                          ...   
ZYG11B                  29.5773531241006             19.0673376256323   
ZYX                     9.47016319225069             644.173691635008   
ZZEF1                   23.4029471173933             8.80908759202247   
ZZZ3                    70.1672037911097             38.3337980800276   
tAKR                   0.162976740692217            0.199871079018115   

            TCGA-E2-A15S-01A-11R-A115-07 TCGA-A2-A1FW-01A-11R-A13Q-07  \
                                                                        
1/2-SBSRNA4             2.76660213716546             2.28447385971219   
A1BG                    14.7424175604732             1.26272158177772   
A1BG-AS1                2.14703912334954            0.862179740068278   
A1CF                  0.0126295721446844           0.0504746695795784   
A2LD1                   2.01753245758846             2.33460165332695   
...                                  ...                          ...   
ZYG11B                  21.8463708185679             29.1821081372339   
ZYX                     60.2257399811681             77.4656969413474   
ZZEF1                   20.6017777750802             26.6416404065616   
ZZZ3                     255.04065475339              60.049575244004   
tAKR                                   0                            0   

            TCGA-HN-A2OB-01A-21R-A27Q-07 TCGA-B6-A0I1-01A-11R-A21T-07  ...  \
                                                                       ...   
1/2-SBSRNA4             2.21287365182981             2.9

This is our cancerous BRCA gene expresion lets save it to CSV and move on to creat a data seth for healthy genes!

In [21]:
BRCA_mutated_data.to_csv("./data/mutatedDataSet.CSV")

In [3]:
with open('./data/GSE62944_RAW/GSM1697009_06_01_15_TCGA_24.normal_Rsubread_TPM.txt') as file:
    healthy_genes=[line.strip().split("\t") for line in file]
healthy_df=pd.DataFrame(healthy_genes)
# Extract first row as column names and shift right
new_columns = [""] + healthy_df.iloc[0, :-1].tolist()  # Shift column names one position right

# Drop the first row since it's now the header
healthy_df = healthy_df.iloc[1:].reset_index(drop=True)

# Assign the new column names
healthy_df.columns = new_columns

healthy_df.head()


TCGA-06-0675-11A-32R-A36H-07 TCGA-06-0678-11A-32R-A36H-07  \
0  1/2-SBSRNA4             3.18073422220701             2.13049012484436   
1         A1BG             7.39732335355717              5.1722413033141   
2     A1BG-AS1             2.59022643394693             1.68470757139805   
3         A1CF           0.0532403304063405            0.017117255111563   
4        A2LD1             3.01460303845154              2.7812473427231   

  TCGA-06-0680-11A-32R-A36H-07 TCGA-06-0681-11A-41R-A36H-07  \
0              2.1761167256058             1.71464925560361   
1             7.30475724374385             11.9796934330644   
2             3.31338461373735             3.30164856662506   
3           0.0303538861837658          0.00615009571388339   
4             2.53074454312974             2.22062308864465   

  TCGA-06-AABW-11A-31R-A36H-07 TCGA-22-4593-11A-01R-1820-07  \
0             1.55566888090254            0.778035365333389   
1             21.0022192919542             3.30495200094336   
2             2.09686636482216            0.879558199010695   
3            0.013585759891076          0.00252059026815952   
4             3.21082563973426             4.09550768491891   

  TCGA-22-4609-11A-01R-2125-07 TCGA-22-5471-11A-01R-1635-07  \
0             1.06999077162721             1.14273389244002   
1             4.70554984193677             2.99717228862688   
2              1.1833657417953             1.25275824298537   
3          0.00413305604933622           0.0183624109151449   
4             3.13388868161999             2.53150787862123   

  TCGA-22-5472-11A-11R-1635-07  ... TCGA-W5-AA2X-11A-11R-A41I-07  \
0            0.881162891368868  ...            0.915108840158311   
1             2.43868352302866  ...             2262.64939429268   
2            0.890781218704234  ...             14.2141996463866   
3          0.00316055082619975  ...             61.7073902545322   
4             3.16419259075836  ...             4.95607024278445   

  TCGA-W5-AA30-11A-11R-A41I-07 TCGA-W5-AA31-11A-11R-A41I-07  \
0            0.293867620204237           0.0871453640505864   
1             2361.61579445944             1548.36672875698   
2             12.1690857458612             10.3758216197413   
3             42.7892256575703             75.5037804880722   
4             3.66514570820693             9.17867627631877   

  TCGA-W5-AA34-11A-11R-A41I-07 TCGA-WA-A7GZ-11A-11R-A34R-07  \
0            0.403677389434792             0.69081426677416   
1             1721.08220718153             1.20945154798853   
2             9.67309575434355            0.358130689763203   
3             67.4564305895944           0.0213472800698393   
4             16.5161945614391             2.64520780223995   

  TCGA-X7-A8D6-11A-22R-A42C-07 TCGA-X7-A8D7-11A-11R-A42C-07  \
0              3.0160903056496             6.26075626091982   
1             10.5106241014704             30.7325961736698   
2             2.68938531241141             4.74297181156493   
3             0.00932020769798           0.0137686732893755   
4             4.72666002042746             4.41406527935657   

  TCGA-Y8-A8RY-11A-11R-A37K-07 TCGA-YB-A89D-11A-11R-A36G-07  \
0             3.78428864815151             1.32437679958846   
1             2.96214515362105             8.78444282548321   
2            0.812348785394276            0.761647232123888   
3           0.0971257068299844            0.845927786570591   
4             7.80396013712328             3.89440685052667   

  TCGA-ZU-A8S4-11A-11R-A41I-07  
0            0.227014015554126  
1             2028.49291424024  
2             11.8723853802107  
3             47.3217659969279  
4             5.55292078404725  

[5 rows x 742 columns]

In [4]:
healthy_df=healthy_df.set_index(healthy_df.columns[0])
healthy_df=healthy_df.loc[:,healthy_genes_sample_dic['BRCA']]
healthy_df.head()

NameError: name 'healthy_genes_sample_dic' is not defined

In [27]:
healthy_df.to_csv("./data/normalDataset.csv")

In [31]:
healthy_df.shape

(23368, 113)

In [1]:
import plotly.graph_objects as go
import plotly.express as px
import numpy as np

# Simulating data (Use your actual healthy_df)
# healthy_df = pd.read_csv("your_data.csv")  # Uncomment to load real data

# Convert DataFrame to long format
# melted_df = healthy_df.stack().reset_index()
# melted_df.columns = ["Gene", "Sample", "Expression Level"]

# Subset only 4 samples for speed
df_subset = healthy_df.iloc[:, :4]

# Convert to long format
melted_df = df_subset.stack().reset_index()
melted_df.columns = ["Gene", "Sample", "Expression Level"]

# Create scatter plot
fig1 = px.scatter(
    melted_df,
    x="Gene",
    y="Sample",
    color="Expression Level",
    color_continuous_scale="Viridis",
    opacity=0.7,  # Adjust opacity for visibility
    title="Gene Expression Scatter Plot (Subset of 4 Samples)"
)

# Turn off axis labels for better readability
fig1.update_layout(
    xaxis_title="Genes",
    yaxis_title="Samples",
    xaxis=dict(showticklabels=False),
    yaxis=dict(showticklabels=False),
    coloraxis_colorbar=dict(title="Expression Level"),
    width=1000, height=800  # Adjust size
)

# Show plot
fig1.show()

NameError: name 'healthy_df' is not defined

In [20]:
stage_sample_diec = {
    'DCIS': ['GSM88859', 'GSM88861', 'GSM88863', 'GSM88865', 'GSM88867', 'GSM88869', 'GSM88871'],
    'IDC': ['GSM88858', 'GSM88860', 'GSM88862', 'GSM88864', 'GSM88866', 'GSM88868', 'GSM88870'],
    'T396': ['GSM88858', 'GSM88859'],
    'T706': ['GSM88860', 'GSM88861'],
    'T796': ['GSM88862', 'GSM88863'],
    'T661': ['GSM88864', 'GSM88865'],
    'T787': ['GSM88866', 'GSM88867'],
    'T808': ['GSM88868', 'GSM88869'],
    'H191': ['GSM88870', 'GSM88871']
}


In [21]:
"""
    since we have found DCIS stage data we now know what genes are expressed in our data set
    lets take a look
"""
import pandas as pd 
DCIS_df = pd.read_csv("expressed_DCIS_Genes.csv", index_col=0)
DCIS_df.head()


IDENTIFIER  GSM88859  GSM88861  GSM88863  GSM88865  GSM88867  \
ID_REF                                                                   
1053_at         RFC2   7.36310   8.80421   7.89757   8.03774   8.02325   
117_at         HSPA6   7.15033   7.54750   7.38728   7.83062   7.48968   
121_at          PAX8   9.42942   9.24060   9.22688   9.55712   9.23641   
1255_g_at     GUCA1A   4.63231   4.75544   4.72679   4.64048   4.65596   
1294_at      MIR5193   8.55953   7.77528   9.99362   8.29521   7.47254   

           GSM88869  GSM88871  GSM88858  GSM88860  GSM88862  GSM88864  \
ID_REF                                                                  
1053_at     8.68432   7.74527   7.64793   7.67504   7.96238   7.80427   
117_at      7.40944   7.38014   7.38607   7.49030   7.76639   7.57006   
121_at      9.43731   9.73340   9.67986   9.27590   9.38470   9.56993   
1255_g_at   4.67152   4.66606   4.77911   4.82142   4.66761   4.75065   
1294_at     8.11136   8.26734   8.26480   7.89782   8.76705   8.82711   

           GSM88866  GSM88868  GSM88870  
ID_REF                                   
1053_at     8.02817   8.54249   7.47866  
117_at      7.48716   7.16147   7.26925  
121_at      9.49319   9.36365   9.67886  
1255_g_at   4.57288   4.69762   4.76414  
1294_at     7.82248   8.35062   8.38374

In [22]:
DCIS_df.columns[1:]

Index(['GSM88859', 'GSM88861', 'GSM88863', 'GSM88865', 'GSM88867', 'GSM88869',
       'GSM88871', 'GSM88858', 'GSM88860', 'GSM88862', 'GSM88864', 'GSM88866',
       'GSM88868', 'GSM88870'],
      dtype='object')

In [23]:
#now change the name of sampples to the stage name
def get_key_from_value(dictionary, target_value):
    for key, value_list in dictionary.items():  # value_list is a list of sample IDs
        if target_value in value_list:  # Check if target_value exists in the list
            return key
    return None 

new_columns_DCIS=[]
for col_name in DCIS_df.columns[1:]:
    new_columns_DCIS.append(get_key_from_value(stage_sample_diec, col_name))
new_columns_DCIS

['DCIS',
 'DCIS',
 'DCIS',
 'DCIS',
 'DCIS',
 'DCIS',
 'DCIS',
 'IDC',
 'IDC',
 'IDC',
 'IDC',
 'IDC',
 'IDC',
 'IDC']

In [24]:
DCIS_df.rename(columns=dict(zip(DCIS_df.columns[1:], new_columns_DCIS)), inplace=True)
DCIS_df.head()

IDENTIFIER     DCIS     DCIS     DCIS     DCIS     DCIS     DCIS  \
ID_REF                                                                       
1053_at         RFC2  7.36310  8.80421  7.89757  8.03774  8.02325  8.68432   
117_at         HSPA6  7.15033  7.54750  7.38728  7.83062  7.48968  7.40944   
121_at          PAX8  9.42942  9.24060  9.22688  9.55712  9.23641  9.43731   
1255_g_at     GUCA1A  4.63231  4.75544  4.72679  4.64048  4.65596  4.67152   
1294_at      MIR5193  8.55953  7.77528  9.99362  8.29521  7.47254  8.11136   

              DCIS      IDC      IDC      IDC      IDC      IDC      IDC  \
ID_REF                                                                     
1053_at    7.74527  7.64793  7.67504  7.96238  7.80427  8.02817  8.54249   
117_at     7.38014  7.38607  7.49030  7.76639  7.57006  7.48716  7.16147   
121_at     9.73340  9.67986  9.27590  9.38470  9.56993  9.49319  9.36365   
1255_g_at  4.66606  4.77911  4.82142  4.66761  4.75065  4.57288  4.69762   
1294_at    8.26734  8.26480  7.89782  8.76705  8.82711  7.82248  8.35062   

               IDC  
ID_REF              
1053_at    7.47866  
117_at     7.26925  
121_at     9.67886  
1255_g_at  4.76414  
1294_at    8.38374

In [25]:
DCIS_df=DCIS_df.set_index(DCIS_df.columns[0])  # Set first column as index
DCIS_df.index.name = None  # Remove index name if necessary
DCIS_df

DCIS     DCIS     DCIS     DCIS     DCIS     DCIS     DCIS  \
RFC2     7.36310  8.80421  7.89757  8.03774  8.02325  8.68432  7.74527   
HSPA6    7.15033  7.54750  7.38728  7.83062  7.48968  7.40944  7.38014   
PAX8     9.42942  9.24060  9.22688  9.55712  9.23641  9.43731  9.73340   
GUCA1A   4.63231  4.75544  4.72679  4.64048  4.65596  4.67152  4.66606   
MIR5193  8.55953  7.77528  9.99362  8.29521  7.47254  8.11136  8.26734   
...          ...      ...      ...      ...      ...      ...      ...   
EHBP1L1  6.17956  6.28655  6.09309  6.27954  6.48258  6.11709  5.92057   
MEX3D    8.32139  8.42359  7.65504  7.80975  8.48139  8.63277  9.26466   
EPS8L1   8.86409  9.03134  8.93064  8.20393  9.34552  8.19034  8.40646   
BCAN     8.23225  8.45223  8.26617  8.23190  8.18839  8.32659  8.31332   
DCAF15   7.25991  7.31001  7.59252  7.42316  7.60465  7.27683  7.37382   

             IDC      IDC      IDC      IDC      IDC      IDC      IDC  
RFC2     7.64793  7.67504  7.96238  7.80427  8.02817  8.54249  7.47866  
HSPA6    7.38607  7.49030  7.76639  7.57006  7.48716  7.16147  7.26925  
PAX8     9.67986  9.27590  9.38470  9.56993  9.49319  9.36365  9.67886  
GUCA1A   4.77911  4.82142  4.66761  4.75065  4.57288  4.69762  4.76414  
MIR5193  8.26480  7.89782  8.76705  8.82711  7.82248  8.35062  8.38374  
...          ...      ...      ...      ...      ...      ...      ...  
EHBP1L1  5.98240  6.06009  6.36389  6.23832  6.82293  7.05653  6.01689  
MEX3D    7.95418  9.13631  7.71274  7.91680  7.76904  7.88847  8.73703  
EPS8L1   8.44893  8.64302  8.76053  8.27957  8.41600  8.03586  8.27489  
BCAN     8.20153  8.08062  8.17031  8.17250  8.21222  8.24798  8.42062  
DCAF15   6.95092  7.20785  7.90691  7.19820  7.51745  7.35828  7.47514  

[54612 rows x 14 columns]

In [26]:
copy_DCIS_df=DCIS_df.copy()

In [27]:
DCIS_df=DCIS_df.groupby(level=0, axis=1).mean()

/var/folders/pd/wynthhk510v_lw3l_4q234gh0000gn/T/ipykernel_51734/1923259962.py:1: FutureWarning:

DataFrame.groupby with axis=1 is deprecated. Do `frame.T.groupby(...)` without axis instead.



In [28]:
import plotly.express as px

fig = px.imshow(DCIS_df.T, 
                labels={'x': "Genes", 'y': "Cancer Type", 'color': "Expression"},
                color_continuous_scale='viridis',  # Better contrast
                aspect='auto')  # Avoids stretching

fig.update_layout(title="Gene Expression Heatmap (DCIS vs IDC)", 
                  xaxis=dict(showticklabels=False))  # Hides gene labels to improve performance

fig.show()

In [29]:
DCIS_df.head()

DCIS       IDC
RFC2     8.079351  7.876991
HSPA6    7.456427  7.447243
PAX8     9.408734  9.492299
GUCA1A   4.678366  4.721919
MIR5193  8.353554  8.330517

In [30]:
# Sort genes by average expression level (for better readability)
DCIS_df_sorted = DCIS_df.sort_values(by='DCIS',ascending=False)

fig = px.imshow(DCIS_df_sorted.T, 
                labels={'x': "Genes", 'y': "Cancer Type", 'color': "Expression"},
                color_continuous_scale='RdBu_r',  # Divergent colormap (Red-Blue)
                aspect='auto')

# Reduce number of x-axis labels to avoid clutter
fig.update_xaxes(showticklabels=False, title="Genes (sorted by expression level)")
fig.update_yaxes(title="Cancer Type")

# Format hover text to show fewer decimal places
fig.update_traces(hovertemplate="Gene: %{x}<br>Cancer Type: %{y}<br>Expression: %{z:.2f}")

# Add a title with better spacing
fig.update_layout(title="Gene Expression Heatmap (DCIS vs IDC)", margin=dict(l=10, r=10, t=40, b=10))

fig.show()

In [31]:
normal_Genes = pd.read_csv("../../data/normalDataSet.csv")
normal_Genes.head()

Unnamed: 0  TCGA-BH-A0DV-11A-22R-A12P-07  TCGA-BH-A0BC-11A-22R-A089-07  \
0  1/2-SBSRNA4                      2.916570                      2.129251   
1         A1BG                      4.583441                      3.430355   
2     A1BG-AS1                      2.074804                      0.594683   
3         A1CF                      0.029291                      0.017338   
4        A2LD1                      3.974090                      4.477155   

   TCGA-BH-A0BM-11A-12R-A089-07  TCGA-AC-A2FB-11A-13R-A17B-07  \
0                      3.888779                      1.751960   
1                      7.794268                      4.969156   
2                      1.531802                      1.423566   
3                      0.026750                      0.007487   
4                      3.073218                      3.735638   

   TCGA-A7-A13E-11A-61R-A12P-07  TCGA-BH-A0BA-11A-22R-A19E-07  \
0                      1.860111                      2.719979   
1                      2.954479                      6.080101   
2                      0.979833                      1.833113   
3                      0.012884                      0.040975   
4                      5.835993                      4.617828   

   TCGA-BH-A1FC-11A-32R-A13Q-07  TCGA-E9-A1R7-11A-42R-A14M-07  \
0                      1.337118                      1.707875   
1                      5.540964                      1.373326   
2                      1.908301                      0.965365   
3                      0.015798                      0.005533   
4                      5.834024                      4.594941   

   TCGA-BH-A0BQ-11A-33R-A115-07  ...  TCGA-BH-A1FB-11A-33R-A13Q-07  \
0                      3.839585  ...                      3.205482   
1                      5.078273  ...                      7.990472   
2                      1.959023  ...                      3.584521   
3                      0.013072  ...                      0.007154   
4                      5.835339  ...                      3.968555   

   TCGA-BH-A0DO-11A-22R-A12D-07  TCGA-BH-A0H7-11A-13R-A089-07  \
0                      3.558338                      2.959784   
1                      6.302861                      8.226531   
2                      1.741917                      1.672998   
3                      0.026669                      0.009589   
4                      4.482055                      4.422212   

   TCGA-BH-A0DD-11A-23R-A12P-07  TCGA-AC-A23H-11A-12R-A157-07  \
0                      0.899846                      2.599581   
1                      1.432410                      2.721933   
2                      0.480103                      1.286758   
3                      0.000000                      0.030975   
4                      4.783359                      3.907226   

   TCGA-BH-A0C3-11A-23R-A12P-07  TCGA-E2-A1IG-11A-22R-A144-07  \
0                      5.403649                      2.031312   
1                      7.486664                      4.874853   
2                      3.153685                      1.825320   
3                      0.033568                      0.021858   
4                      3.562723                      4.496156   

   TCGA-BH-A18S-11A-43R-A12D-07  TCGA-BH-A0BJ-11A-23R-A089-07  \
0                      1.714944                      2.544465   
1                      7.077226                      5.233371   
2                      2.667175                      2.052595   
3                      0.026497                      0.052270   
4                      3.326848                      3.793690   

   TCGA-BH-A0H5-11A-62R-A115-07  
0                      4.870535  
1                     10.022869  
2                      2.631513  
3                      0.068109  
4                      6.280192  

[5 rows x 114 columns]

In [32]:
DCIS_df.index

Index(['RFC2', 'HSPA6', 'PAX8', 'GUCA1A', 'MIR5193', 'THRA', 'PTPN21', 'CCL5',
       'CYP2E1', 'EPHB3',
       ...
       'LRCH4', 'LRTM1', 'MIR1306', '91682_at', 'EXOSC4', 'EHBP1L1', 'MEX3D',
       'EPS8L1', 'BCAN', 'DCAF15'],
      dtype='object', length=54612)

In [33]:
normal_Genes=normal_Genes.rename(columns={'Unnamed: 0':'Genes'})
normal_Genes=normal_Genes[normal_Genes['Genes'].isin(DCIS_df.index)]
normal_Genes

Genes  TCGA-BH-A0DV-11A-22R-A12P-07  TCGA-BH-A0BC-11A-22R-A089-07  \
1          A1BG                      4.583441                      3.430355   
2      A1BG-AS1                      2.074804                      0.594683   
3          A1CF                      0.029291                      0.017338   
5           A2M                    891.304796                   1027.552125   
6         A2ML1                      0.407684                      1.591699   
...         ...                           ...                           ...   
23362    ZYG11A                      2.341758                      0.941305   
23363    ZYG11B                     25.447914                     15.618164   
23364       ZYX                    423.349725                    422.733835   
23365     ZZEF1                     25.409044                     21.584477   
23366      ZZZ3                     56.440822                     33.466630   

       TCGA-BH-A0BM-11A-12R-A089-07  TCGA-AC-A2FB-11A-13R-A17B-07  \
1                          7.794268                      4.969156   
2                          1.531802                      1.423566   
3                          0.026750                      0.007487   
5                        769.492283                   1219.532714   
6                          2.157845                      0.565392   
...                             ...                           ...   
23362                      1.205575                      0.643131   
23363                     15.296591                     17.201148   
23364                    498.626093                    402.401882   
23365                     15.564758                     19.346944   
23366                     37.029402                     31.258128   

       TCGA-A7-A13E-11A-61R-A12P-07  TCGA-BH-A0BA-11A-22R-A19E-07  \
1                          2.954479                      6.080101   
2                          0.979833                      1.833113   
3                          0.012884                      0.040975   
5                       1519.749915                   1031.124367   
6                          0.320481                      0.897928   
...                             ...                           ...   
23362                      1.509081                      1.767445   
23363                     22.768192                     27.022879   
23364                    258.380481                    309.136839   
23365                     23.007421                     26.795460   
23366                     28.341837                     37.211808   

       TCGA-BH-A1FC-11A-32R-A13Q-07  TCGA-E9-A1R7-11A-42R-A14M-07  \
1                          5.540964                      1.373326   
2                          1.908301                      0.965365   
3                          0.015798                      0.005533   
5                       1197.183488                   1398.533894   
6                          0.294743                      0.511213   
...                             ...                           ...   
23362                      2.837455                      0.345649   
23363                     18.831835                     33.187092   
23364                    407.244301                    201.186402   
23365                     17.769314                     24.777163   
23366                     32.072816                     37.929890   

       TCGA-BH-A0BQ-11A-33R-A115-07  ...  TCGA-BH-A1FB-11A-33R-A13Q-07  \
1                          5.078273  ...                      7.990472   
2                          1.959023  ...                      3.584521   
3                          0.013072  ...                      0.007154   
5                       1339.187209  ...                    741.943041   
6                          1.974174  ...                      0.343201   
...                             ...  ...                           ...   
23362                      2.610163  ...                

In [34]:
#do the same process for malignant genes
malignant_genes = pd.read_csv("../../data/mutatedDataSet.csv")
malignant_genes=malignant_genes.rename(columns={'Unnamed: 0':'Genes'})
malignant_genes=malignant_genes[malignant_genes['Genes'].isin(DCIS_df.index)]
malignant_genes

Genes  TCGA-A2-A0T1-01A-21R-A084-07  TCGA-A7-A3J0-01A-11R-A213-07  \
1          A1BG                      3.554418                     24.851102   
2      A1BG-AS1                      1.126241                      3.723119   
3          A1CF                      0.008392                      0.000000   
5           A2M                    425.868340                    156.271227   
6         A2ML1                      3.488973                      0.492898   
...         ...                           ...                           ...   
23362    ZYG11A                      0.805060                      0.350474   
23363    ZYG11B                     10.871916                     12.243353   
23364       ZYX                    365.273345                    152.190475   
23365     ZZEF1                     12.108496                     27.451921   
23366      ZZZ3                     12.356083                     22.993002   

       TCGA-AO-A126-01A-11R-A10J-07  TCGA-E2-A14X-01A-11R-A115-07  \
1                         37.604899                      3.148319   
2                          1.530582                      1.783702   
3                          0.029567                      0.048623   
5                        300.640797                    406.091231   
6                          0.112573                     22.525628   
...                             ...                           ...   
23362                      1.177963                      2.335984   
23363                      9.135284                     18.695474   
23364                    254.570885                    227.541749   
23365                      5.888063                     16.285927   
23366                     23.834492                     44.800121   

       TCGA-A7-A13G-01A-11R-A13Q-07  TCGA-AR-A0TP-01A-11R-A084-07  \
1                          4.088710                     11.884501   
2                          1.725531                      2.119275   
3                          0.341332                      0.014651   
5                         98.289505                   6985.208108   
6                          0.382082                      0.164870   
...                             ...                           ...   
23362                      4.835798                      2.778470   
23363                     29.577353                     19.067338   
23364                      9.470163                    644.173692   
23365                     23.402947                      8.809088   
23366                     70.167204                     38.333798   

       TCGA-E2-A15S-01A-11R-A115-07  TCGA-A2-A1FW-01A-11R-A13Q-07  \
1                         14.742418                      1.262722   
2                          2.147039                      0.862180   
3                          0.012630                      0.050475   
5                        236.668156                    337.779713   
6                          0.231883                      0.252745   
...                             ...                           ...   
23362                      8.387578                      7.166327   
23363                     21.846371                     29.182108   
23364                     60.225740                     77.465697   
23365                     20.601778                     26.641640   
23366                    255.040655                     60.049575   

       TCGA-HN-A2OB-01A-21R-A27Q-07  ...  TCGA-A2-A0YJ-01A-11R-A109-07  \
1                         19.940351  ...                      3.397926   
2                          3.096331  ...                      1.151397   
3                          0.000000  ...                      0.000000   
5                        561.773513  ...                    100.929053   
6                          0.349747  ...                     39.667941   
...                             ...  ...                           ...   
23362                      1.785013  ...                

Now we have all the data related to breast cancer

In [35]:
#letsSave updated data frame and continue the ahp analysis
normal_Genes.to_csv("../../data/DCIS_IDC_Normal.csv", index=False)
malignant_genes.to_csv("../../data/DCIS_IDC_Malignant.csv", index=False)

In [41]:
copy_DCIS_df.reset_index().rename(columns={'index':'Gene'}).to_csv("DCIS_renamed_data.csv", index=False)